<a href="https://www.kaggle.com/code/jorgeluiscruzquispe/la-molina-uhi?scriptVersionId=183856652" target="_blank"><img align="left" alt="Kaggle" title="Open in Kaggle" src="https://kaggle.com/static/images/open-in-kaggle.svg"></a>

# <center><i>UHI del distrito de La Molina</i></center>
---

In [1]:
!pip install -q leafmap
!pip install -q geemap

In [2]:
def polygon_contour(gdf):
    
    contorno = gdf.total_bounds
    
    polygon = shapely.geometry.Polygon([
        (contorno[0], contorno[1]),
        (contorno[0], contorno[3]),
        (contorno[2], contorno[3]),
        (contorno[2], contorno[1]),
        (contorno[0], contorno[1]),
    ])

    polygon_gdf = gpd.GeoDataFrame(geometry = [polygon], crs = str(gdf.crs))
    
    polygon_gdf["Tipo"] = "Area de influencia"
    
    polygon_gdf["Area (hec)"] = round(polygon_gdf.geometry.area[0]/10000, 2)
    
    return polygon_gdf

def add_centroides(feature):
    
    centroid = feature.geometry().centroid() 
    
    return ee.Feature(centroid).copyProperties(feature) 

In [3]:
import geopandas as gpd
import pandas as pd
import geemap.foliumap as geemap
import leafmap.foliumap as leafmap
import geemap.colormaps as cmap
import shapely
import ee

In [4]:
ee.Authenticate()
ee.Initialize()

In [5]:
gdf = gpd.read_file("/kaggle/input/manzanas-la-molina/LA_MOLINA_LIMA_150114_Manzanas_Poblacion_JuanPablo_SuyoPomalia_geogpsperu_931381206.shp", crs = 4326)
gdf.drop(columns = ["contacto", "descargar", "whatsapp", "ARCHIVO", "Nombre", "Apellido"], inplace = True)
gdf.to_crs(32718, inplace = True)

In [6]:
gdf.ZONA.unique()

array(['00700', '02500', '00300', '00200', '00400', '01000', '02200',
       '01400', '01200', '02100', '01900', '01300', '00500', '00100',
       '02300', '01700', '01500', '01600', '02000', '00900', '00600',
       '02400', '00800', '01800', '01100'], dtype=object)

In [8]:
gdf_contour = polygon_contour(gdf)

In [51]:
gdf.explore("ZONA", cmap = "Spectral", tiles = "CartoDB dark_matter")

In [9]:
Map = leafmap.Map()

Map.add_basemap("HYBRID")

Map.add_gdf(gdf_contour, style = {"color": "red", "fillOpacity": 0}, layer_name = "layer2")

Map.add_gdf(gdf, style = {"color": "orange", "fillOpacity": 0}, layer_name = "layer1")

Map

In [10]:
contour = geemap.gdf_to_ee(gdf_contour)

lamolina = geemap.gdf_to_ee(gdf)

In [11]:
Map = geemap.Map()

Map.centerObject(contour)

Map.addLayer(ee.Image().paint(contour, 0, 2), {"palette": "black"}, "Contorno de Distrito")

Map.addLayer(ee.Image().paint(lamolina, 0, 2), {"palette": "red"}, "Distrito")

Map

In [12]:
image = ee.ImageCollection('LANDSAT/LC08/C02/T1')\
                    .filterMetadata('CLOUD_COVER_LAND', 'less_than', 2).filterBounds(contour).first()

In [13]:
Map = geemap.Map()

Map.centerObject(contour)

Map.addLayer(image, {}, "Imagen satelital")

Map.addLayer(ee.Image().paint(contour, 0, 2), {"palette": "black"}, "Contorno de Distrito")

Map.addLayer(ee.Image().paint(lamolina, 0, 2), {"palette": "red"}, "Distrito")

Map

In [14]:
image.bandNames().getInfo()

['B1',
 'B2',
 'B3',
 'B4',
 'B5',
 'B6',
 'B7',
 'B8',
 'B9',
 'B10',
 'B11',
 'QA_PIXEL',
 'QA_RADSAT',
 'SAA',
 'SZA',
 'VAA',
 'VZA']

In [16]:
metadata = image.getInfo()["properties"]

metadata_filtrada = dict(filter(lambda item: item[0].startswith('K'), metadata.items()))

In [17]:
metadata_filtrada

{'K2_CONSTANT_BAND_11': 1201.1442,
 'K2_CONSTANT_BAND_10': 1321.0789,
 'K1_CONSTANT_BAND_10': 774.8853,
 'K1_CONSTANT_BAND_11': 480.8883}

In [35]:
TOA = image.select("B10").multiply(0.0003342).add(0.1).subtract(0.29)

BT = ((((TOA.divide(774.8853)).pow(-1).add(1).log()).divide(1321.0789)).pow(-1)).subtract(273.15).rename(['BT'])

NDVI = image.expression('(B5 - B4)/(B5 + B4)', 
                            {
                                'B4': image.select("B4"),
                                'B5': image.select("B5"),                                
                            }
                       ).rename(['NDVI'])

PV = NDVI.add(0.4106880128383637).divide(0.6583547592160386 + 0.4106880128383637).rename(["PV"])

E = image.expression('0.004*PV + 0.986', {'PV': PV.select("PV")}).rename(['E'])

LST = ee.Image().expression('BT / (1 + (10.8 * (BT / 14388)) * log(E))',
                            {
                                'BT': BT.select("BT"),
                                'E': E.select("E"),
                            }
                           ).rename(['LST'])

LST_mean =  list(LST.reduceRegion(ee.Reducer.mean(), scale = 100).getInfo().values())[0]

LST_stdDev = list(LST.reduceRegion(ee.Reducer.stdDev(), scale = 100).getInfo().values())[0]

UHI = LST.subtract(LST_mean).divide(LST_stdDev).rename(["UHI"])

In [36]:
temp_molina = UHI.clip(lamolina)

min_ = list(UHI.reduceRegion(ee.Reducer.min(), scale = 100, geometry = lamolina).getInfo().values())[0]

max_ = list(UHI.reduceRegion(ee.Reducer.max(), scale = 100, geometry = lamolina).getInfo().values())[0]

Map = geemap.Map()

Map.add_basemap("HYBRID")

Map.centerObject(contour)

Map.addLayer(temp_molina, {"palette": cmap.palettes.jet, "min": min_, "max": max_}, "layer")

Map.addLayer(ee.Image().paint(lamolina, 0, 0.75), {"palette": "red"}, "Distrito")

Map

In [37]:
centroides = lamolina.map(add_centroides)

In [38]:
Map = geemap.Map()

Map.add_basemap("HYBRID")

Map.centerObject(centroides)

Map.addLayer(ee.Image().paint(lamolina, 0, 0.75), {"palette": "red"}, "Distrito")

Map.addLayer(centroides, {"color": "blue"}, "Centroides")

Map

In [39]:
centroides_temp = temp_molina.sampleRegions(
    collection = centroides,
    scale = 30,   
    geometries = True
)

In [40]:
gdf_cent_temp = geemap.ee_to_gdf(centroides_temp)

gdf_cent_temp =  gdf_cent_temp[["UHI", "LLAVE_MZS"]]

In [41]:
gdf_temp_lamolina = pd.concat([gdf, gdf_cent_temp], axis = 1)

gdf_temp_lamolina.drop(columns = ["LLAVE_MZS"], inplace = True)

In [46]:
gdf_temp_lamolina.explore("UHI", cmap = "jet", tiles = "OpenStreetMap", legend = True)

In [47]:
gdf_temp_lamolina.to_file("lamolina_UHI.shp")